# Ray Tune

In this notebook, we turn to hyperparameter tuning using Ray. 

Our objective is to use ray tune to find better :

* achitecture
* optimizer
* learning rate


@Date: 03-Oct-2020 | @Author: Katnoria

In [8]:
import os
from datetime import datetime
import matplotlib.pyplot as plt

import tensorflow as tf
import tensorflow_datasets as tfds
from tensorflow.keras.layers import Dense, Flatten, Conv2D, MaxPool2D, Dropout
from tensorflow.keras.layers import BatchNormalization, Input, GlobalAveragePooling2D
from tensorflow.keras import Model

# tuner
import ray
from ray import tune
from ray.tune.integration.keras import TuneReporterCallback

In [9]:
def version_info(cls):
    print(f"{cls.__name__}: {cls.__version__}")

In [10]:
print("Version Used in this Notebook:")
version_info(tf)
version_info(tfds)
version_info(ray)

Version Used in this Notebook:
tensorflow: 2.3.0
tensorflow_datasets: 3.2.1
ray: 0.8.7


In [11]:
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))

Num GPUs Available:  1


In [12]:
gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
  # Restrict TensorFlow to only use the first GPU
  try:
    tf.config.experimental.set_visible_devices(gpus[0], 'GPU')
    logical_gpus = tf.config.experimental.list_logical_devices('GPU')
    print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPU")
  except RuntimeError as e:
    # Visible devices must be set before GPUs have been initialized
    print(e)

1 Physical GPUs, 1 Logical GPU


# Dataset

Tensorflow Datasets already provides this dataset in a format that we can use out of the box.

In [13]:
# Load the dataset
(ds_train, ds_test), metadata = tfds.load(
    'cifar10', split=['train', 'test'], shuffle_files=True, 
    with_info=True, as_supervised=True
)

In [14]:
len(ds_train), len(ds_test), metadata.features['label'].num_classes

(50000, 10000, 10)

Use the built in function to visualise the dataset 

In [15]:
# Review metadata
# See https://www.tensorflow.org/datasets/overview
metadata.features

FeaturesDict({
    'id': Text(shape=(), dtype=tf.string),
    'image': Image(shape=(32, 32, 3), dtype=tf.uint8),
    'label': ClassLabel(shape=(), dtype=tf.int64, num_classes=10),
})

In [16]:
NUM_CLASSES = metadata.features["label"].num_classes

num_train_examples = len(ds_train)
num_test_examples = len(ds_test)
print(f"Training dataset size: {num_train_examples}")
print(f"Test dataset size: {num_test_examples}")

Training dataset size: 50000
Test dataset size: 10000


## Plot Images

Next, we plot some images from the training data

In [17]:
examples = ds_train.take(64)

fig, axs = plt.subplots(5, 5, figsize=(8,8))

for record, ax in zip(examples, axs.flat):
    image, _ = record
    ax.imshow(image)
    ax.axis('off')
plt.show()

# RAY Tune

In the previous notebooks, we manually tried different hyperparameters. Now, we are going to automate that process and use ray to find the best hyperparams. 

We need to define the following:

* objective to maximise
* hyperparam search space
* search algorithm to find best hyperparams


# Use Pretrained Models
Instead of training the full model, it is generally a good practice to use a pretrained network as a base model and add your layers on top. This allows us to reduce the training times and leverage on what base model has learned.

### Define Model

We will create our model that will accept hyperparams from the trainer. We are going to determine the best dropout rate, hidden units and activation to use in order to improve the model accuracy

In [18]:
class CIFAR10Model(Model):
    def __init__(self, base_model, num_classes, drop_rate=0.1, hidden_units=128, hidden_activation='relu'):
        super(CIFAR10Model, self).__init__()
        self.base_model = base_model
        self.base_model.trainable = False
        self.dropout = Dropout(drop_rate)
        self.fc1 = Dense(hidden_units, activation=hidden_activation)
        self.fc2 = Dense(num_classes)
        
    def call(self, x):
        x = self.base_model(x)
        x = GlobalAveragePooling2D()(x)
        x = self.fc1(x)
        x = self.dropout(x)
        return self.fc2(x)        

### Trainable

This is where you will setup the model initialisation and training. `tune.run` will run this class instance  with different hyperparams based on the config

In [19]:
# Reference: https://docs.ray.io/en/latest/tune/examples/tf_mnist_example.html
class CIFAR10Trainable(tune.Trainable):

    def load_data(self, batch_size):
        (ds_train, ds_test), metadata = tfds.load(
            'cifar10', split=['train', 'test'], shuffle_files=True, 
            with_info=True, as_supervised=True
        )        
        num_classes = metadata.features["label"].num_classes
        
        train_ds = ds_train \
            .cache() \
            .shuffle(num_train_examples).batch(batch_size, drop_remainder=True) \
            .prefetch(tf.data.experimental.AUTOTUNE)      
        
        test_ds = ds_test \
            .cache() \
            .batch(batch_size, drop_remainder=True) \
            .prefetch(tf.data.experimental.AUTOTUNE)         
        
        return train_ds, test_ds, num_classes
    
    def setup(self, config):
        import tensorflow as tf
        IMG_SIZE = 32
        BATCH_SIZE = 128
        # load data
        self.train_ds, self.test_ds, num_classes = self.load_data(BATCH_SIZE)
        # model
        base_model = tf.keras.applications.ResNet50(input_shape=(IMG_SIZE, IMG_SIZE, 3), include_top=False)
        self.model = CIFAR10Model(
            base_model,
            num_classes,
            config.get("drop_rate", 0.1),
            config.get("hidden_units", 128),
            config.get("activation", "relu")
        )
        # set loss & optimizer
        self.loss_object = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
        self.optimizer = tf.keras.optimizers.Adam(config.get("lr", 1e-3))
        # set train and test metrics
        self.train_loss = tf.keras.metrics.Mean(name="train_loss")
        self.train_accuracy = tf.keras.metrics.SparseCategoricalAccuracy(name="train_accuracy")
        self.test_loss = tf.keras.metrics.Mean(name="test_loss")
        self.test_accuracy = tf.keras.metrics.SparseCategoricalAccuracy(name="test_accuracy")
        
        @tf.function
        def train_step(images, labels):
            with tf.GradientTape() as tape:
                predictions = self.model(images)
                loss = self.loss_object(labels, predictions)
            gradients = tape.gradient(loss, self.model.trainable_variables)
            self.optimizer.apply_gradients(
                zip(gradients, self.model.trainable_variables)
            )
            # record metric
            self.train_loss(loss)
            self.train_accuracy(labels, predictions)
        
        @tf.function
        def test_step(images, labels):
            predictions = self.model(images)
            test_loss = self.loss_object(labels, predictions)            
            # record metric
            self.test_loss(test_loss)
            self.test_accuracy(labels, predictions)
        
        self.tf_train_step = train_step
        self.tf_test_step = test_step
        
    def step(self):
        # reset state
        self.train_loss.reset_states()
        self.train_accuracy.reset_states()
        self.test_loss.reset_states()
        self.test_accuracy.reset_states()
        # train step
        for images, labels in self.train_ds:
            self.tf_train_step(images, labels)
        # test step
        for images, labels in self.test_ds:
            self.tf_test_step(images, labels)
            
        return {
            "epoch": self.iteration,
            "loss": self.train_loss.result().numpy(),
            "accuracy": self.train_accuracy.result().numpy()*100,
            "test_loss": self.test_loss.result().numpy(),
            "mean_accuracy": self.test_accuracy.result().numpy()*100,
        }        

### Setup Config

For config explanation, refer [docs](https://docs.ray.io/en/master/tune/api_docs/search_space.html#tune-sample-docs)

In [20]:
config = {
    "hidden_units": tune.grid_search([32, 64, 128, 256]),
#     "drop_rate": tune.quniform(0.0,0.8, 0.2), # says no attribute?
    "drop_rate": tune.uniform(0, 1),
    "activation": tune.choice(['elu', 'relu', 'selu']),
    "lr": tune.loguniform(1e-4, 1e-2)
}

In [21]:
analysis = tune.run(
    CIFAR10Trainable,
    config=config,
    num_samples=10,
    stop={"training_iteration": 25},
     resources_per_trial={"cpu": 6, "gpu": 1}
)

2020-10-04 16:21:00,186	INFO resource_spec.py:231 -- Starting Ray with 77.29 GiB memory available for workers and up to 37.13 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-10-04 16:21:00,953	INFO services.py:1193 -- View the Ray dashboard at localhost:8265


(pid=29566) 2020-10-04 16:21:02.218078: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
(pid=29561) 2020-10-04 16:21:02.228171: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcudart.so.10.1
(pid=29561) 2020-10-04 16:21:03.586234: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=29566) 2020-10-04 16:21:03.576789: I tensorflow/stream_executor/platform/default/dso_loader.cc:48] Successfully opened dynamic library libcuda.so.1
(pid=29561) 2020-10-04 16:21:03.726988: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1716] Found device 0 with properties: 
(pid=29561) pciBusID: 0000:01:00.0 name: GeForce GTX 1080 Ti computeCapability: 6.1
(pid=29561) coreClock: 1.683GHz coreCount: 28 deviceMemorySize: 10.91GiB deviceMemoryBandwidth: 451.17GiB/s
(pid=29561) 2020-10-04 16:21:03.727028: I tensorflow/str

Result for CIFAR10Trainable_899dd_00001:
  accuracy: 52.373796701431274
  date: 2020-10-04_16-21-19
  done: false
  epoch: 0
  experiment_id: 5219c5d9d4a94429b94f06c7355e4330
  experiment_tag: 1_activation=selu,drop_rate=0.27307,hidden_units=64,lr=0.00067646
  hostname: ironman
  iterations_since_restore: 1
  loss: 1.4190818071365356
  mean_accuracy: 58.55368375778198
  node_ip: 192.168.86.61
  pid: 29561
  test_loss: 1.1799941062927246
  time_since_restore: 13.045613050460815
  time_this_iter_s: 13.045613050460815
  time_total_s: 13.045613050460815
  timestamp: 1601799679
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 899dd_00001
  


Result for CIFAR10Trainable_899dd_00001:
  accuracy: 62.19150424003601
  date: 2020-10-04_16-21-25
  done: false
  epoch: 1
  experiment_id: 5219c5d9d4a94429b94f06c7355e4330
  experiment_tag: 1_activation=selu,drop_rate=0.27307,hidden_units=64,lr=0.00067646
  hostname: ironman
  iterations_since_restore: 2
  loss: 1.0800284147262573
  mean_accuracy: 60.516828298568726
  node_ip: 192.168.86.61
  pid: 29561
  test_loss: 1.1387135982513428
  time_since_restore: 19.10733389854431
  time_this_iter_s: 6.061720848083496
  time_total_s: 19.10733389854431
  timestamp: 1601799685
  timesteps_since_restore: 0
  training_iteration: 2
  trial_id: 899dd_00001
  


Result for CIFAR10Trainable_899dd_00001:
  accuracy: 65.42868614196777
  date: 2020-10-04_16-21-31
  done: false
  epoch: 2
  experiment_id: 5219c5d9d4a94429b94f06c7355e4330
  experiment_tag: 1_activation=selu,drop_rate=0.27307,hidden_units=64,lr=0.00067646
  hostname: ironman
  iterations_since_restore: 3
  loss: 0.978851854801178
  mean_accuracy: 61.58854365348816
  node_ip: 192.168.86.61
  pid: 29561
  test_loss: 1.116542935371399
  time_since_restore: 25.169443130493164
  time_this_iter_s: 6.0621092319488525
  time_total_s: 25.169443130493164
  timestamp: 1601799691
  timesteps_since_restore: 0
  training_iteration: 3
  trial_id: 899dd_00001
  


...

Result for CIFAR10Trainable_899dd_00038:
  accuracy: 81.79687261581421
  date: 2020-10-04_18-02-12
  done: false
  epoch: 20
  experiment_id: 93378312ba894c77ae991899d5c83908
  experiment_tag: 38_activation=elu,drop_rate=0.81403,hidden_units=128,lr=0.0035282
  hostname: ironman
  iterations_since_restore: 21
  loss: 0.5127376317977905
  mean_accuracy: 58.40344429016113
  node_ip: 192.168.86.61
  pid: 16280
  test_loss: 1.8232752084732056
  time_since_restore: 696.0698421001434
  time_this_iter_s: 31.280486345291138
  time_total_s: 696.0698421001434
  timestamp: 1601805732
  timesteps_since_restore: 0
  training_iteration: 21
  trial_id: 899dd_00038
  


Result for CIFAR10Trainable_899dd_00038:
  accuracy: 82.30568766593933
  date: 2020-10-04_18-02-43
  done: false
  epoch: 21
  experiment_id: 93378312ba894c77ae991899d5c83908
  experiment_tag: 38_activation=elu,drop_rate=0.81403,hidden_units=128,lr=0.0035282
  hostname: ironman
  iterations_since_restore: 22
  loss: 0.49355337023735046
  mean_accuracy: 57.77243375778198
  node_ip: 192.168.86.61
  pid: 16280
  test_loss: 1.935581922531128
  time_since_restore: 727.2840993404388
  time_this_iter_s: 31.21425724029541
  time_total_s: 727.2840993404388
  timestamp: 1601805763
  timesteps_since_restore: 0
  training_iteration: 22
  trial_id: 899dd_00038
  


Result for CIFAR10Trainable_899dd_00038:
  accuracy: 83.28725695610046
  date: 2020-10-04_18-03-14
  done: false
  epoch: 22
  experiment_id: 93378312ba894c77ae991899d5c83908
  experiment_tag: 38_activation=elu,drop_rate=0.81403,hidden_units=128,lr=0.0035282
  hostname: ironman
  iterations_since_restore: 23
  loss: 0.46818917989730835
  mean_accuracy: 58.2932710647583
  node_ip: 192.168.86.61
  pid: 16280
  test_loss: 1.9937084913253784
  time_since_restore: 758.3407638072968
  time_this_iter_s: 31.05666446685791
  time_total_s: 758.3407638072968
  timestamp: 1601805794
  timesteps_since_restore: 0
  training_iteration: 23
  trial_id: 899dd_00038
  


Result for CIFAR10Trainable_899dd_00038:
  accuracy: 83.23317170143127
  date: 2020-10-04_18-03-45
  done: false
  epoch: 23
  experiment_id: 93378312ba894c77ae991899d5c83908
  experiment_tag: 38_activation=elu,drop_rate=0.81403,hidden_units=128,lr=0.0035282
  hostname: ironman
  iterations_since_restore: 24
  loss: 0.46868962049484253
  mean_accuracy: 57.992786169052124
  node_ip: 192.168.86.61
  pid: 16280
  test_loss: 2.0331454277038574
  time_since_restore: 789.6290209293365
  time_this_iter_s: 31.288257122039795
  time_total_s: 789.6290209293365
  timestamp: 1601805825
  timesteps_since_restore: 0
  training_iteration: 24
  trial_id: 899dd_00038
  


Result for CIFAR10Trainable_899dd_00038:
  accuracy: 84.00440812110901
  date: 2020-10-04_18-04-17
  done: true
  epoch: 24
  experiment_id: 93378312ba894c77ae991899d5c83908
  experiment_tag: 38_activation=elu,drop_rate=0.81403,hidden_units=128,lr=0.0035282
  hostname: ironman
  iterations_since_restore: 25
  loss: 0.45232176780700684
  mean_accuracy: 57.97275900840759
  node_ip: 192.168.86.61
  pid: 16280
  test_loss: 2.0949580669403076
  time_since_restore: 821.4502458572388
  time_this_iter_s: 31.82122492790222
  time_total_s: 821.4502458572388
  timestamp: 1601805857
  timesteps_since_restore: 0
  training_iteration: 25
  trial_id: 899dd_00038
  


In [31]:
analysis.get_best_config()

# Report

In [3]:
import pandas as pd

In [27]:
df = analysis.dataframe()
df

epoch      loss   accuracy  test_loss  mean_accuracy  done  \
0      24  0.596869  79.447114   1.398472      59.415066  True   
1      24  0.237505  92.433894   2.020007      59.014422  True   
2      24  0.780748  73.161060   1.645024      57.051283  True   
3      24  0.821100  71.508414   1.534269      58.834136  True   
4      24  0.991048  65.184295   1.274288      57.572114  True   
5      24  0.602937  78.431493   1.664063      58.653843  True   
6      24  0.560520  79.951924   1.918573      58.022839  True   
7      24  0.100192  98.227161   1.744703      60.937500  True   
8      24  0.589073  79.797679   1.325508      60.236377  True   
9      24  0.460897  83.102965   2.103375      57.722354  True   
10     24  0.359003  87.119389   2.294650      57.872593  True   
11     24  0.106113  96.260017   3.125494      58.994389  True   
12     24  0.762453  73.717946   1.141981      61.838943  True   
13     24  0.605076  80.126202   1.189030      61.227965  True   
14     24  0.267321  90.546876   2.727681      57.622194  True   
15     24  0.025067  99.827725   2.301123      60.366589  True   
16     24  0.643604  78.225160   1.248287      60.927486  True   
17     24  0.368741  88.529646   1.495735      60.346556  True   
18     24  0.079935  97.940707   2.358328      59.154648  True   
19     24  0.082526  98.932290   1.739097      60.847354  True   
20     24  0.582045  80.112177   1.298052      60.757214  True   
21     24  0.518388  81.384212   1.849694      57.672274  True   
22     24  0.393966  85.889423   2.207310      57.491988  True   
23     24  0.085758  97.391826   2.323400      60.376602  True   
24     24  0.741954  73.868191   1.364747      59.855771  True   
25     24  0.466896  85.016024   1.284634      62.039262  True   
26     24  0.183021  93.345350   2.906452      58.002806  True   
27     24  0.130547  95.396632   2.973763      58.593750  True   
28     24  0.560162  80.538863   1.407532      59.194714  True   
29     24  0.586832  80.749196   1.199788      61.919069  True   
30     24  0.474605  84.975964   1.227253      61.979169  True   
31     24  0.069637  97.812498   2.992084      59.575319  True   
32     24  0.637711  78.205127   1.273925      60.286456  True   
33     24  0.217990  92.906648   2.139115      58.203125  True   
34     24  0.223587  94.296873   1.553773      60.556889  True   
35     24  0.075741  97.431892   3.212335      59.194714  True   
36     24  0.799241  71.786857   1.342921      59.675479  True   
37     24  0.604849  78.553689   1.621096      58.143032  True   
38     24  0.452322  84.004408   2.094958      57.972759  True   
39     24  0.205554  95.422679   1.419304      61.288059  True   

    timesteps_total  episodes_total  training_iteration  \
0               NaN             NaN                  25   
1               NaN             NaN                  25   
2               NaN             NaN                  25   
3               NaN             NaN                  25   
4               NaN             NaN                  25   
5               NaN             NaN                  25   
6               NaN             NaN                  25   
7               NaN             NaN                  25   
8               NaN             NaN                  25   
9               NaN             NaN                  25   
10              NaN             NaN                  25   
11              NaN             NaN                  25   
12              NaN             NaN                  25   
13              NaN             NaN                  25   
14              NaN             NaN                  25   
15              NaN             NaN                  25   
16              NaN             NaN                  25   
17              NaN             NaN                  25   
18              NaN             NaN                  25   
19              NaN             NaN                  25   
20              NaN             NaN                  25   

In [32]:
# Best mean accuracy
df['mean_accuracy'].max()

62.03926205635071

In [36]:
# Row with the best mean accuracy
df[df['mean_accuracy'] == df['mean_accuracy'].max()]

epoch      loss   accuracy  test_loss  mean_accuracy  done  \
25     24  0.466896  85.016024   1.284634      62.039262  True   

    timesteps_total  episodes_total  training_iteration  \
25              NaN             NaN                  25   

                       experiment_id  ... time_since_restore  \
25  d6e4147aa30e4a3483a5325d73f92961  ...         885.731203   

    timesteps_since_restore  iterations_since_restore     trial_id  \
25                        0                        25  899dd_00025   

                                       experiment_tag config/activation  \
25  25_activation=elu,drop_rate=0.40079,hidden_uni...               elu   

   config/drop_rate  config/hidden_units  config/lr  \
25          0.40079                   64   0.000199   

                                               logdir  
25  /home/ashish/ray_results/CIFAR10Trainable/CIFA...  

[1 rows x 27 columns]

In [37]:
# best train accuracy
df[df['accuracy'] == df['accuracy'].max()]

epoch      loss   accuracy  test_loss  mean_accuracy  done  \
15     24  0.025067  99.827725   2.301123      60.366589  True   

    timesteps_total  episodes_total  training_iteration  \
15              NaN             NaN                  25   

                       experiment_id  ... time_since_restore  \
15  076cfb754cab4862a461e0ea9320e2b2  ...         163.025278   

    timesteps_since_restore  iterations_since_restore     trial_id  \
15                        0                        25  899dd_00015   

                                       experiment_tag config/activation  \
15  15_activation=relu,drop_rate=0.6837,hidden_uni...              relu   

   config/drop_rate  config/hidden_units  config/lr  \
15         0.683699                  256    0.00043   

                                               logdir  
15  /home/ashish/ray_results/CIFAR10Trainable/CIFA...  

[1 rows x 27 columns]

In [28]:
df.to_csv("v1-analysis.csv")